## Contexto del Dataset
Este dataset es originario del Sistema de Vigilancia de Salud Pública (SIVIGILA), que recopila y analiza datos sobre eventos que afectan la salud de la población colombiana como enfermedades (infecciosas, crónicas, etc.), factores de riesgo y otros sucesos de importancia en salud pública.

## Descripción del Problema
TODO: hacer descripción de la problematica

Para llevar acabo este caso de uso, se utilizará el conjunto de datos disponible en: https://portalsivigila.ins.gov.co/Paginas/Buscador.aspx

En el presente trabajo se pretende realizar un realizar un análisis exploratorio, limpieza, modelado y evaluación sobre el conjunto de datos epidemiológicos obtenidos del sistema SIVIGILA (Colombia) centrado en la patologia DENGUE en el periodo 2022-2024.

#### Objetivos específicos:
- Realizar análisis y pruebas con el dataset.
- Aplicar técnicas de procesamiento al conjunto de datos.
- Implementar modelos de aprendizaje de máquina.

### Importar librerias

In [15]:
# Esto hace que cada vez que ejecutes una celda, Jupyter verifique si algún módulo local cambió y lo recargue automáticamente.
%load_ext autoreload 
%autoreload 2

# Importar las librerías necesarias
from ydata_profiling import ProfileReport, compare
import pandas as pd
from pathlib import Path
import sys

# Agregar el directorio raíz del proyecto al sys.path para permitir importaciones de utilidades realizadas
project_root = Path.cwd().parent
sys.path.insert(0, str(project_root))

# Importar el modulo de utilidades desde el paquete src
from src import data_utils, visualization_utils


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


### Carga Datos
En esta sección se realiza la conversión de formato a los archivos descargados desde el portal del SIVIGILA, utilizando el módulo de utilidades.
Con la finalidad de acelerar el proceso posterior de cargado y lectura, dicha conversión se hará de formato .xlsx -> formato .parquet

In [ ]:
data_utils.convertir_excel_a_parquet()

Una vez realizada la conversión procedemos a cargar los datos en un diccionario usando el módulo de utilidades, de esta manera obtendremos los nombres de los archivos asociados a sus respectivos dataframes


In [4]:
dict_df = data_utils.cargar_archivos_parquet()

Se cargaron 3 archivos Parquet desde C:\Users\edavi\OneDrive - Universidad del Magdalena\Universidad\8° Semestre\ia\ml-analyst-sivigila\data\processed
Nombres de los archivos cargados: ['Datos_2022_210', 'Datos_2023_210', 'Datos_2024_210']


Verificamos si existen inconsistencias en las columnas de los distintos DataFrames y mostramos el DataFrame de referencia para realizar una primera inspección:

In [13]:
df_ref, columnas_en_comun = data_utils.verificar_referencia_columnas(dict_df)


El Archivo de referencia para las columnas es: 'Datos_2024_210'

Diferencias encontradas en el archivo'Datos_2022_210':
Columnas adicionales no presentes en el archivo de referencia:
    - consecutive_origen (tipo actual: int64)

Diferencias encontradas en el archivo'Datos_2023_210':
Columnas adicionales no presentes en el archivo de referencia:
    - consecutive_origen (tipo actual: int64)



A partir de esta revisión, se concluye que la única inconsistencia identificada a nivel de columnas corresponde al campo consecutive_origen, el cual no se encuentra en el archivo de datos de 2024 pero sí en los de 2022 y 2023.
Asimismo, se confirma que no existen columnas duplicadas ni diferencias en los nombres de las variables entre los conjuntos de datos.
En consecuencia, procederemos a unir los DataFrames en un único conjunto consolidado, con el fin de realizar el análisis exploratorio y las etapas posteriores de limpieza y procesamiento.

In [6]:
df = data_utils.unir_df(dict_df)

### EDA INICIAL
Realizaremos un primer EDA (Exploratory Data Analysis) sobre los datos crudos después de unir los Dataframes y antes de limpiar con el objetivo de entender la naturaleza y calidad del dataset

In [18]:

profile = ProfileReport(
    df, 
    title="Perfil inicial de los datos crudos", 
    minimal=True, 
    progress_bar=False
)

report_dir = "reports/01_initial_data_profile.html"
report_path = project_root / report_dir

profile.to_file(report_path)
profile.to_notebook_iframe()
visualization_utils.show_report_link(report_dir)
df

100%|██████████| 73/73 [00:11<00:00,  6.59it/s]


Reporte generado: https://edmh1.github.io/ml-analyst-sivigila/reports/01_initial_data_profile.html


CONSECUTIVE  COD_EVE     FEC_NOT  SEMANA   ANO     COD_PRE  COD_SUB  \
0           8915475      210  2022-09-30      39  2022  8541000080        1   
1           8915476      210  2022-02-07       5  2022  8501000190        1   
2           8915477      210  2022-04-08      13  2022  8500100001        3   
3           8908033      210  2022-04-04      13  2022  8500100001        3   
4           8908034      210  2022-05-16      19  2022  5000600169        1   
...             ...      ...         ...     ...   ...         ...      ...   
501724     11747636      210  2024-01-20       3  2024  1300100542        1   
501725     11747515      210  2024-04-09      13  2024  7683404652        1   
501726     10899536      210  2024-07-22      16  2024  6300100354        1   
501727     11652745      210  2024-02-13       2  2024  7600103799        1   
501728     11652771      210  2024-03-08      10  2024   800104669        1   

        EDAD  UNI_MED  nacionalidad  ...  \
0         19        1           170  ...   
1         18        1           170  ...   
2         19        1           170  ...   
3          8        1           170  ...   
4          8        1           170  ...   
...      ...      ...           ...  ...   
501724    24        1           170  ...   
501725    21        1           170  ...   
501726    25        1           170  ...   
501727     5        1            32  ...   
501728    27        1            32  ...   

                                                 Nom_upgd Pais_ocurrencia  \
0                         ESE HOSPITAL LOCAL DE TAURAMENA        COLOMBIA   
1            HOSPITAL DE AGUAZUL JUAN HERNANDO URREGO ESE        COLOMBIA   
2                        HOSPITAL DE YOPAL ESE NUEVA SEDE        COLOMBIA   
3                        HOSPITAL DE YOPAL ESE NUEVA SEDE        COLOMBIA   
4                           HOSPITAL MUNICIPAL DE ACACIAS        COLOMBIA   
...                                                   ...             ...   
501724  CLINICA MADRE BERNARDA COMUNIDAD DE HERMANAS F...        COLOMBIA   
501725                   HOSPITAL DPTAL TOMAS URIBE URIBE        COLOMBIA   
501726  ESE HOSPITAL DEPTAL UNIVERSITARIO SAN JUAN DE ...        COLOMBIA   
501727   HOSPITAL UNIVERSITARIO DEL VALLE EVARISTO GARCIA       ARGENTINA   
501728                          ORTOCLINIC DEL CARIBE SAS       ARGENTINA   

        Nombre_evento  Departamento_ocurrencia  Municipio_ocurrencia  \
0              DENGUE                 CASANARE             TAURAMENA   
1              DENGUE                 CASANARE               AGUAZUL   
2              DENGUE                 CASANARE             TAURAMENA   
3              DENGUE                 CASANARE                 YOPAL   
4              DENGUE                     META               ACACIAS   
...               ...                      ...                   ...   
501724         DENGUE                  BOLIVAR             CARTAGENA   
501725         DENGUE                    VALLE                 TULUA   
501726         DENGUE                  QUINDIO               ARMENIA   
501727         DENGUE                 EXTERIOR    EXTERIOR_ARGENTINA   
501728         DENGUE                 EXTERIOR    EXTERIOR_ARGENTINA   

        Pais_residencia Departamento_residencia Municipio_residencia  \
0              COLOMBIA                CASANARE            TAURAMENA   
1              COLOMBIA                CASANARE              AGUAZUL   
2              COLOMBIA                CASANARE            TAURAMENA   
3              COLOMBIA                CASANARE                YOPAL   
4              COLOMBIA                    META              ACACIAS   
...                 ...                     ...                  ...   
501724         COLOMBIA                 BOLIVAR            CARTAGENA   
501725         COLOMBIA                   VALLE                TULUA   
501726          FRANCIA                EXTERIOR     EXTERIOR_FRANCIA   
501727         COLOM

El dataset consta de 501.729 entradas y 73 columnas. Para realizar la inspección de cada una de las columnas se toma como referencia las descripcones dadas por el Instituto Nacional de Salud en Colombia
en el archivo diccionario-datos-basicos-sivigila.pdf que se pueden encontrar en la carpeta references descargado desde: https://www.ins.gov.co/BibliotecaDigital/diccionario-datos-basicos-sivigila.pdf

In [ ]:
##**TODO:** limpiar y transformar el dataframe `df` antes de guardarlo.

Una vez solucionados los problemas de consistencia en las columnas en nuestro conjunto de datos se procede a unificar todos los archivos y
guardarlos en un unico archivo de extensión parquet que será el archivo con el que se trabajara durante todo el análisis

In [ ]:
data_utils.guardar_df(df, 'datos_full')

En esta sección se realiza la lectura del archivo parquet previamente generado, con el fin de disponer de los datos unificados para su posterior análisis.

In [ ]:
df = pd.read_parquet('../data/processed/datos_full.parquet')

### Analisis del dataframe limpio

In [ ]:
df.info()

In [ ]:
profile = ProfileReport(
    df,
    title="Análisis de Perfil de Datos",
    minimal=True,
    progress_bar=False,
)
profile.to_notebook_iframe()

**TODO:** Descripción de analisis de perfil de datos